# NBA Dataset EDA

## Libraries and Dependencies

In [35]:
pip install statsmodels

Note: you may need to restart the kernel to use updated packages.


In [36]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sqlalchemy.engine import create_engine
import sqlite3 as sql3
from pandas.io import sql
import plotly.express as px
import plotly.graph_objects as go
import subprocess
import os
import warnings
warnings.filterwarnings('ignore')
%load_ext sql

The sql extension is already loaded. To reload it, use:
  %reload_ext sql


In [37]:
# Establish connection to SQL database
conn = sql3.connect('nba.sqlite')
conn

In [38]:
# View table names
tables = pd.read_sql_query(
    "SELECT name FROM sqlite_master WHERE type = 'table'", conn)
print(tables)

                   name
0                  game
1          game_summary
2           other_stats
3             officials
4      inactive_players
5             game_info
6            line_score
7          play_by_play
8                player
9                  team
10   common_player_info
11         team_details
12         team_history
13  draft_combine_stats
14        draft_history
15     team_info_common
16   avg_team_game_data
17        all_shot_data


## EDA

In [39]:
# EDA::
# 2003-2004 season through 2022-2023 season
# Team win percentage as home & away
# Team wins based on game location
# Using UNION to display wins as both home and away
query = """
                SELECT 
                    (season_id - 20000) AS season,
                    team_id_home AS team_id,
                    team_name_home AS team_name,
                    SUM(CASE wl_home
                            WHEN 'W' THEN 1
                            ELSE 0
                        END) AS wins,
                    COUNT(team_id_home) AS games_played,
                    "home" AS game_location
                FROM game
                WHERE season >= 2000
                GROUP BY season_id, team_id_home
                
                UNION
                
                SELECT (season_id - 20000) AS season,
                    team_id_away AS team_id,
                    team_name_away AS team_name,
                    SUM(CASE wl_away
                            WHEN 'W' THEN 1
                            ELSE 0
                        END) AS wins,
                    COUNT(team_id_away) AS games_played,
                    "away" AS game_location
                FROM game
                WHERE season >= 2000
                GROUP BY season_id, team_id_away;
                """
team_game_stats = pd.read_sql(query, conn)
team_game_stats["win_percentage"] = round(100 * 
                                          team_game_stats["wins"] / 
                                          team_game_stats["games_played"], 2
                                         )
team_game_stats

season     team_id            team_name  wins  games_played  \
0       2000  1610612737        Atlanta Hawks     7            41   
1       2000  1610612737        Atlanta Hawks    18            41   
2       2000  1610612738       Boston Celtics    16            41   
3       2000  1610612738       Boston Celtics    20            41   
4       2000  1610612739  Cleveland Cavaliers    10            41   
...      ...         ...                  ...   ...           ...   
1307    2022  1610612764   Washington Wizards    16            36   
1308    2022  1610612765      Detroit Pistons     7            33   
1309    2022  1610612765      Detroit Pistons     8            35   
1310    2022  1610612766    Charlotte Hornets    11            33   
1311    2022  1610612766    Charlotte Hornets    11            37   

     game_location  win_percentage  
0             away           17.07  
1             home           43.90  
2             away           39.02  
3             home           48.78  
4             away           24.39  
...            ...             ...  
1307          away           44.44  
1308          away           21.21  
1309          home           22.86  
1310          home           33.33  
1311          away           29.73  

[1312 rows x 7 columns]

In [40]:
# Comparison between games won at home vs away over 20 years
game_loc_df = pd.DataFrame(team_game_stats, columns=['season', 'team_id', 'team_name', 'wins',
                                                     'games_played', 'game_location', 'win_percentage'])

game_loc_scatter = px.scatter(game_loc_df, x="season", y="win_percentage",
                              color="game_location", size="wins", hover_name="team_name"
                             )
game_loc_scatter.update_xaxes(nticks=20)
game_loc_scatter.show()

In [41]:
# 2003-2004 season through 2022-2023 season
# Team overall win percentage
# team_overall_win_pct
query = """
        SELECT
          season,
          team_id,
          team_name,
          SUM(wins) AS total_wins,
          SUM(games_played) AS total_games_played,
          (SUM(wins) * 100.0 / SUM(games_played)) AS win_percentage
        FROM
          (
            SELECT
              (season_id - 20000) AS season,
              team_id_home AS team_id,
              team_name_home AS team_name,
              SUM(CASE wl_home
                      WHEN 'W' THEN 1
                      ELSE 0
                  END) AS wins,
              COUNT(team_id_home) AS games_played
            FROM game
            WHERE season >= 2000
            GROUP BY
              season_id,
              team_id_home

            UNION ALL

            SELECT
              (season_id - 20000) AS season,
              team_id_away AS team_id,
              team_name_away AS team_name,
              SUM(CASE wl_away
                      WHEN 'W' THEN 1
                      ELSE 0
                  END) AS wins,
              COUNT(team_id_away) AS games_played
            FROM game
            WHERE season >= 2000
            GROUP BY
              season_id,
              team_id_away
          ) AS subquery
        GROUP BY
          season,
          team_id,
          team_name;
        """
team_overall_win_pct = pd.read_sql(query, conn)
team_overall_win_pct

season     team_id            team_name  total_wins  total_games_played  \
0      2000  1610612737        Atlanta Hawks          25                  82   
1      2000  1610612738       Boston Celtics          36                  82   
2      2000  1610612739  Cleveland Cavaliers          30                  82   
3      2000  1610612741        Chicago Bulls          15                  82   
4      2000  1610612742     Dallas Mavericks          53                  82   
..      ...         ...                  ...         ...                 ...   
651    2022  1610612762            Utah Jazz          33                  68   
652    2022  1610612763    Memphis Grizzlies          40                  65   
653    2022  1610612764   Washington Wizards          31                  68   
654    2022  1610612765      Detroit Pistons          15                  68   
655    2022  1610612766    Charlotte Hornets          22                  70   

     win_percentage  
0         30.487805  
1         43.902439  
2         36.585366  
3         18.292683  
4         64.634146  
..              ...  
651       48.529412  
652       61.538462  
653       45.588235  
654       22.058824  
655       31.428571  

[656 rows x 6 columns]

In [42]:
# Win percentage by team from 2000 - 2023: Scatter
win_pct_df = pd.DataFrame(team_overall_win_pct, columns=['season', 'team_id', 'team_name',
                                                         'total_wins', 'total_games_played',
                                                         'win_percentage']
                         )

win_pct_scatter = px.scatter(win_pct_df, x="season", y="win_percentage",
                             color="total_wins", size="total_wins", hover_name="team_name"
                            )
win_pct_scatter.update_xaxes(nticks=20)
win_pct_scatter.show()

In [43]:
query = """
        SELECT 
            (season_id - 20000) AS season,
            team_id_home AS team_id,
            team_name_home AS team_name,
            wl_home AS w_l,
            fga_home AS fga,
            fgm_home AS fgm,
            fg3a_home AS fg3a,
            fg3m_home AS fg3m,
            fta_home AS fta,
            ftm_home AS ftm,
            fg_pct_home AS fg_pct,
            fg3_pct_home AS fg3_pct,
            ft_pct_home AS ft_pct,
            reb_home AS rebounds,
            ast_home AS assists,
            stl_home AS steals,
            blk_home AS blocks,
            tov_home AS turnovers,
            pts_home AS points,
            "home" AS game_location
        FROM game
        WHERE season >= 2000

        UNION

        SELECT (season_id - 20000) AS season,
            team_id_away AS team_id,
            team_name_away AS team_name,
            wl_away AS w_l,
            fga_away AS fga,
            fgm_away AS fgm,
            fg3a_away AS fg3a,
            fg3m_away AS fg3m,
            fta_away AS fta,
            ftm_away AS ftm,
            fg_pct_away AS fg_pct,
            fg3_pct_away AS fg3_pct,
            ft_pct_away AS ft_pct,
            reb_away AS rebounds,
            ast_away AS assists,
            stl_away AS steals,
            blk_away AS blocks,
            tov_away AS turnovers,
            pts_away AS points,
            "away" AS game_location
        FROM game
        WHERE season >= 2000
        """
team_shot_stats_all = pd.read_sql(query, conn)
team_shot_stats_all

season     team_id          team_name w_l    fga   fgm  fg3a  fg3m  \
0        2000  1610612737      Atlanta Hawks   L   69.0  27.0  15.0   5.0   
1        2000  1610612737      Atlanta Hawks   L   69.0  31.0   6.0   1.0   
2        2000  1610612737      Atlanta Hawks   L   69.0  31.0  10.0   5.0   
3        2000  1610612737      Atlanta Hawks   L   70.0  28.0   9.0   3.0   
4        2000  1610612737      Atlanta Hawks   L   70.0  28.0   9.0   4.0   
...       ...         ...                ...  ..    ...   ...   ...   ...   
52241    2022  1610612766  Charlotte Hornets   W   95.0  49.0  31.0  10.0   
52242    2022  1610612766  Charlotte Hornets   W   96.0  43.0  35.0  14.0   
52243    2022  1610612766  Charlotte Hornets   W   96.0  48.0  36.0   9.0   
52244    2022  1610612766  Charlotte Hornets   W  102.0  43.0  31.0  10.0   
52245    2022  1610612766  Charlotte Hornets   W  102.0  53.0  48.0  20.0   

        fta   ftm  fg_pct  fg3_pct  ft_pct  rebounds  assists  steals  blocks  \
0      23.0  15.0   0.391    0.333   0.652      43.0     17.0     8.0     2.0   
1      25.0  19.0   0.449    0.167   0.760      48.0     14.0    13.0     5.0   
2      41.0  35.0   0.449    0.500   0.854      34.0     20.0     6.0     2.0   
3      23.0  19.0   0.400    0.333   0.826      49.0     11.0     7.0     8.0   
4      25.0  16.0   0.400    0.444   0.640      52.0     13.0     4.0     5.0   
...     ...   ...     ...      ...     ...       ...      ...     ...     ...   
52241  23.0  17.0   0.516    0.323   0.739      56.0     26.0     4.0     7.0   
52242  29.0  20.0   0.448    0.400   0.690      58.0     26.0     8.0    12.0   
52243  25.0  17.0   0.500    0.250   0.680      37.0     27.0    14.0    10.0   
52244  31.0  24.0   0.422    0.323   0.774      55.0     32.0     2.0     2.0   
52245  19.0  12.0   0.520    0.417   0.632      49.0     32.0    11.0     3.0   

       turnovers  points game_location  
0           24.0      74          away  
1           27.0      82          away  
2           20.0     102          home  
3           22.0      78          home  
4           23.0      76          away  
...          ...     ...           ...  
52241       14.0     125          away  
52242       16.0     120          home  
52243       10.0     122          away  
52244       10.0     120          home  
52245        5.0     138          away  

[52246 rows x 20 columns]

In [44]:
# Comparing field goal attempts to field goal percent
team_accuracy = pd.DataFrame(
    team_shot_stats_all, columns=['season', 'team_id', 'team_name',
                                  'fga', 'fgm', 'fg3a', 'fg3m', 'fta', 'ftm',
                                  'fg_pct', 'fg3_pct', 'ft_pct', 'game_location']
)
accuracy_scatter = px.scatter(team_accuracy, x="fga", y="fg_pct", color="game_location",
                              opacity=0.4, hover_name="team_name")
accuracy_scatter.update_traces(marker_size=5)
accuracy_scatter.show()

In [45]:
# Add 2-point shooting variables to team_shot_stats_all

team_shot_stats_all["fg2a"] = (team_shot_stats_all["fga"] - team_shot_stats_all["fg3a"])
team_shot_stats_all["fg2m"] = (team_shot_stats_all["fgm"] - team_shot_stats_all["fg3m"])
team_shot_stats_all["fg2_pct"] = round(100 * team_shot_stats_all["fg2m"] / 
                                       team_shot_stats_all["fg2a"], 2)
team_shot_stats_all = team_shot_stats_all[['season', 'team_id', 'team_name', 'w_l',
                                           'fga', 'fgm', 'fg2a', 'fg2m', 'fg3a', 'fg3m', 
                                           'fta', 'ftm','fg_pct', 'fg2_pct', 'fg3_pct', 
                                           'ft_pct', 'rebounds', 'assists', 'steals', 'blocks', 
                                           'turnovers', 'points', 'game_location']]
team_shot_stats_all
# Scale percent variables
team_shot_stats_all["fg_pct"] = round(100 * team_shot_stats_all["fgm"] / 
                                       team_shot_stats_all["fga"], 2)
team_shot_stats_all.fg_pct
team_shot_stats_all["fg3_pct"] = round(100 * team_shot_stats_all["fg3m"] / 
                                       team_shot_stats_all["fg3a"], 2)
team_shot_stats_all.fg3_pct
team_shot_stats_all["ft_pct"] = round(100 * team_shot_stats_all["ftm"] / 
                                       team_shot_stats_all["fta"], 2)
team_shot_stats_all.ft_pct

0        65.22
1        76.00
2        85.37
3        82.61
4        64.00
         ...  
52241    73.91
52242    68.97
52243    68.00
52244    77.42
52245    63.16
Name: ft_pct, Length: 52246, dtype: float64

In [46]:
# Find averages for each variable
team_avg_stats = team_shot_stats_all.groupby(
    ['season', 'team_name', 'game_location']).mean().reset_index()
print(team_avg_stats)

      season           team_name game_location        fga        fgm  \
0       2000       Atlanta Hawks          away  81.097561  33.682927   
1       2000       Atlanta Hawks          home  81.536585  36.463415   
2       2000      Boston Celtics          away  78.390244  33.780488   
3       2000      Boston Celtics          home  79.780488  33.853659   
4       2000   Charlotte Hornets          away  78.707317  33.341463   
...      ...                 ...           ...        ...        ...   
1307    2022     Toronto Raptors          home  90.393939  41.393939   
1308    2022           Utah Jazz          away  89.228571  42.028571   
1309    2022           Utah Jazz          home  88.060606  41.606061   
1310    2022  Washington Wizards          away  86.638889  42.138889   
1311    2022  Washington Wizards          home  83.687500  40.656250   

           fg2a       fg2m       fg3a       fg3m        fta  ...     fg_pct  \
0     70.682927  30.243902  10.414634   3.439024  21.073

In [47]:
# Exploring average shooting stats
# Comparing 3-point attempts to points scored, by game location
avg_fg2 = px.scatter(team_avg_stats, x="fg2a", y="points", size="fg2m",
                     animation_frame="season", animation_group="team_name", 
                     color="game_location", hover_name = "team_name",
                     facet_col="game_location", range_x=[20, 100], range_y=[50, 140]
                    )
avg_fg2.show()
# Here we see that average 2-point attempts are slightly higher when teams play at home.
# We also see that the number of 2-point attempts decreases over the years, while 
# the average total points per game increases. 

In [48]:
# Exploring average shooting stats
# Comparing 3-point attempts to points scored, by game location
avg_fg3 = px.scatter(team_avg_stats, x="fg3a", y="points", size="fg3m",
                     animation_frame="season", animation_group="team_name", 
                     color="game_location", facet_col="game_location", 
                     hover_name = "team_name", range_x=[0, 60], range_y=[50, 140]
                    )
avg_fg3.show()
# Here we see that average 3-point attempts are slightly higher at home, however it is unclear how
# significant the difference is, and we will need to test for effect size.
# Average 3-point attempts increase significantly (roughly doubling) over the years, and
# points increase at a similar rate (not surprisingly).

In [49]:
team_avg_stats = team_avg_stats.merge(
    team_game_stats[['season', 'team_name', 'game_location', 'wins', 'games_played', 'win_percentage']], 
    on = ['season', 'team_name', 'game_location'], how = 'left'
)
team_avg_stats

season           team_name game_location        fga        fgm  \
0       2000       Atlanta Hawks          away  81.097561  33.682927   
1       2000       Atlanta Hawks          home  81.536585  36.463415   
2       2000      Boston Celtics          away  78.390244  33.780488   
3       2000      Boston Celtics          home  79.780488  33.853659   
4       2000   Charlotte Hornets          away  78.707317  33.341463   
...      ...                 ...           ...        ...        ...   
1307    2022     Toronto Raptors          home  90.393939  41.393939   
1308    2022           Utah Jazz          away  89.228571  42.028571   
1309    2022           Utah Jazz          home  88.060606  41.606061   
1310    2022  Washington Wizards          away  86.638889  42.138889   
1311    2022  Washington Wizards          home  83.687500  40.656250   

           fg2a       fg2m       fg3a       fg3m        fta  ...     ft_pct  \
0     70.682927  30.243902  10.414634   3.439024  21.073171  ...  77.743415   
1     69.195122  31.780488  12.341463   4.682927  23.097561  ...  75.372195   
2     57.463415  26.195122  20.926829   7.585366  26.975610  ...  73.081951   
3     60.878049  27.000000  18.902439   6.853659  26.439024  ...  74.185610   
4     66.365854  28.829268  12.341463   4.512195  26.731707  ...  74.304146   
...         ...        ...        ...        ...        ...  ...        ...   
1307  58.848485  30.727273  31.545455  10.666667  25.545455  ...  77.759697   
1308  51.828571  29.114286  37.400000  12.914286  21.457143  ...  79.443714   
1309  48.848485  27.151515  39.212121  14.454545  26.515152  ...  77.498182   
1310  56.361111  31.916667  30.277778  10.222222  24.250000  ...  75.556944   
1311  52.000000  28.437500  31.687500  12.218750  20.437500  ...  83.398125   

       rebounds    assists    steals    blocks  turnovers      points  wins  \
0     43.268293  19.146341  7.707317  5.365854  17.829268   86.951220     7   
1     42.536585  18.878049  7.756098  4.073171  15.536585   94.975610    18   
2     37.756098  20.902439  9.292683  4.341463  15.390244   94.975610    16   
3     41.853659  20.756098  9.463415  3.853659  15.951220   94.268293    20   
4     44.487805  20.560976  7.682927  5.243902  14.756098   91.048780    18   
...         ...        ...       ...       ...        ...         ...   ...   
1307  43.696970  23.272727  9.454545  5.181818  11.757576  113.363636    20   
1308  43.428571  25.685714  6.228571  5.171429  14.742857  114.142857    13   
1309  46.606061  24.939394  6.515152  5.424242  16.212121  118.393939    20   
1310  43.750000  24.833333  7.055556  5.222222  13.750000  112.777778    16   
1311  42.343750  25.281250  6.531250  5.093750  14.625000  110.500000    15   

      games_played  win_percentage  
0               41           17.07  
1               41           43.90  
2               41           39.02  
3               41           48.78  
4               41           43.90  
...            ...             ...  
1307            33           60.61  
1308            35           37.14  
1309            33           60.61  
1310            36           44.44  
1311            32           46.88  

[1312 rows x 24 columns]

In [50]:
# Import our Team Average Stats dataframe into our SQL database
# Grouped by Season and Team Name
team_avg_stats.to_sql('avg_team_game_data', con = conn, if_exists = 'replace')

# Import total shooting stats dataframe into SQL database
# Data for each game played
team_shot_stats_all.to_sql('all_shot_data', con = conn, if_exists = 'replace')


52246

In [51]:
# Create a dataframe for each team
cursor = conn.cursor()
cursor.execute(
    "SELECT DISTINCT team_name FROM avg_team_game_data")

team_names = [row[0] for row in cursor.fetchall()]
team_dataframes = {}

for team_name in team_names:
    query = f"SELECT * FROM avg_team_game_data WHERE team_name = '{team_name}'"
    team_dataframes[team_name] = pd.read_sql_query(query, conn)

print(team_names)
for team_name, dataframe in team_dataframes.items():
    team_variable_name = team_name.replace(" ", "_").replace("/", "_").lower() + "_data"
    globals()[team_variable_name] = dataframe
list(team_avg_stats)

['Atlanta Hawks', 'Boston Celtics', 'Charlotte Hornets', 'Chicago Bulls', 'Cleveland Cavaliers', 'Dallas Mavericks', 'Denver Nuggets', 'Detroit Pistons', 'Golden State Warriors', 'Houston Rockets', 'Indiana Pacers', 'Los Angeles Clippers', 'Los Angeles Lakers', 'Miami Heat', 'Milwaukee Bucks', 'Minnesota Timberwolves', 'New Jersey Nets', 'New York Knicks', 'Orlando Magic', 'Philadelphia 76ers', 'Phoenix Suns', 'Portland Trail Blazers', 'Sacramento Kings', 'San Antonio Spurs', 'Seattle SuperSonics', 'Toronto Raptors', 'Utah Jazz', 'Vancouver Grizzlies', 'Washington Wizards', 'Memphis Grizzlies', 'New Orleans Hornets', 'Charlotte Bobcats', 'New Orleans/Oklahoma City Hornets', 'Oklahoma City Thunder', 'Brooklyn Nets', 'New Orleans Pelicans', 'LA Clippers']


['season',
 'team_name',
 'game_location',
 'fga',
 'fgm',
 'fg2a',
 'fg2m',
 'fg3a',
 'fg3m',
 'fta',
 'ftm',
 'fg_pct',
 'fg2_pct',
 'fg3_pct',
 'ft_pct',
 'rebounds',
 'assists',
 'steals',
 'blocks',
 'turnovers',
 'points',
 'wins',
 'games_played',
 'win_percentage']

In [52]:
# Identify yearly scoring trends by win percentage

In [53]:
# Field goals

query = """
        SELECT
            season,
            team_name,
            SUM(wins) AS wins,
            SUM(games_played) AS games,
            win_percentage,
            AVG(points) AS points,
            AVG(fga) AS field_goal_attempts,
            AVG(fgm) AS field_goals_made,
            AVG(fg_pct) AS field_goal_percent
        FROM
            avg_team_game_data
        GROUP BY
            season,
            team_name;
        """
season_fg_wins = pd.read_sql(query, conn)
season_fg_wins

season            team_name  wins  games  win_percentage      points  \
0      2000        Atlanta Hawks    25     82           17.07   90.963415   
1      2000       Boston Celtics    36     82           39.02   94.621951   
2      2000    Charlotte Hornets    46     82           43.90   91.939024   
3      2000        Chicago Bulls    15     82           12.20   87.573171   
4      2000  Cleveland Cavaliers    30     82           24.39   92.207317   
..      ...                  ...   ...    ...             ...         ...   
651    2022     Sacramento Kings    40     66           59.38  121.118566   
652    2022    San Antonio Spurs    17     67           18.18  111.245544   
653    2022      Toronto Raptors    32     68           34.29  112.410390   
654    2022            Utah Jazz    33     68           37.14  116.268398   
655    2022   Washington Wizards    31     68           44.44  111.638889   

     field_goal_attempts  field_goals_made  field_goal_percent  
0              81.317073         35.073171           43.131829  
1              79.085366         33.817073           42.848780  
2              79.280488         34.146341           43.287805  
3              78.182927         33.182927           42.555976  
4              79.658537         35.243902           44.342927  
..                   ...               ...                 ...  
651            87.496324         43.708640           49.959311  
652            91.131907         42.553030           46.984211  
653            90.925541         41.339827           45.606069  
654            88.644589         41.817316           47.178524  
655            85.163194         41.397569           48.729792  

[656 rows x 9 columns]

In [54]:
# Field Goals by points and season
fg_scatter = px.scatter(
    season_fg_wins, x="points", y="field_goal_percent", size = "win_percentage", 
    color="field_goal_percent", animation_frame = "season", animation_group = "team_name", 
    hover_name = "team_name", size_max = 20, range_x=[80, 130], range_y=[35, 55]
)

fg_scatter.show()

In [55]:
# 2 Point Shots
query = """
        SELECT
            season,
            team_name,
            SUM(wins) AS wins,
            SUM(games_played) AS games,
            win_percentage,
            AVG(points) AS points,
            AVG(fg2a) AS two_point_attempts,
            AVG(fg2m) AS two_points_made,
            AVG(fg2_pct) AS two_point_percent
        FROM
            avg_team_game_data
        GROUP BY
            season,
            team_name;
        """
season_fg2_wins = pd.read_sql(query, conn)
season_fg2_wins

season            team_name  wins  games  win_percentage      points  \
0      2000        Atlanta Hawks    25     82           17.07   90.963415   
1      2000       Boston Celtics    36     82           39.02   94.621951   
2      2000    Charlotte Hornets    46     82           43.90   91.939024   
3      2000        Chicago Bulls    15     82           12.20   87.573171   
4      2000  Cleveland Cavaliers    30     82           24.39   92.207317   
..      ...                  ...   ...    ...             ...         ...   
651    2022     Sacramento Kings    40     66           59.38  121.118566   
652    2022    San Antonio Spurs    17     67           18.18  111.245544   
653    2022      Toronto Raptors    32     68           34.29  112.410390   
654    2022            Utah Jazz    33     68           37.14  116.268398   
655    2022   Washington Wizards    31     68           44.44  111.638889   

     two_point_attempts  two_points_made  two_point_percent  
0             69.939024        31.012195          44.383171  
1             59.170732        26.597561          45.133537  
2             67.280488        30.000000          44.892439  
3             66.597561        29.170732          43.837561  
4             71.621951        32.560976          45.583415  
..                  ...              ...                ...  
651           51.214154        30.316176          59.174807  
652           60.323975        32.044563          53.285477  
653           58.867100        30.535065          52.024957  
654           50.338528        28.132900          56.034394  
655           54.180556        30.177083          55.712292  

[656 rows x 9 columns]

In [56]:
# 2 Point Field Goals by points and season
fg2_scatter = px.scatter(
    season_fg2_wins, x="points", y="two_point_percent", size = "win_percentage", 
    color="two_point_percent", animation_frame = "season", animation_group = "team_name", 
    hover_name = "team_name", size_max = 20, range_x=[80, 130], range_y=[35, 65]
)

fg2_scatter.show()

In [57]:
# 3 Point Shots
query = """
        SELECT
            season,
            team_name,
            SUM(wins) AS wins,
            SUM(games_played) AS games,
            win_percentage,
            AVG(points) AS points,
            AVG(fg3a) AS three_point_attempts,
            AVG(fg3m) AS three_points_made,
            AVG(fg3_pct) AS three_point_percent
        FROM
            avg_team_game_data
        GROUP BY
            season,
            team_name;
        """
season_fg3_wins = pd.read_sql(query, conn)
season_fg3_wins

season            team_name  wins  games  win_percentage      points  \
0      2000        Atlanta Hawks    25     82           17.07   90.963415   
1      2000       Boston Celtics    36     82           39.02   94.621951   
2      2000    Charlotte Hornets    46     82           43.90   91.939024   
3      2000        Chicago Bulls    15     82           12.20   87.573171   
4      2000  Cleveland Cavaliers    30     82           24.39   92.207317   
..      ...                  ...   ...    ...             ...         ...   
651    2022     Sacramento Kings    40     66           59.38  121.118566   
652    2022    San Antonio Spurs    17     67           18.18  111.245544   
653    2022      Toronto Raptors    32     68           34.29  112.410390   
654    2022            Utah Jazz    33     68           37.14  116.268398   
655    2022   Washington Wizards    31     68           44.44  111.638889   

     three_point_attempts  three_points_made  three_point_percent  
0               11.378049           4.060976            35.928049  
1               19.914634           7.219512            35.680610  
2               12.000000           4.146341            34.022195  
3               11.585366           4.012195            34.765732  
4                8.036585           2.682927            31.756707  
..                    ...                ...                  ...  
651             36.282169          13.392463            36.853686  
652             30.807932          10.508467            34.386546  
653             32.058442          10.804762            33.816216  
654             38.306061          13.684416            35.637519  
655             30.982639          11.220486            35.830365  

[656 rows x 9 columns]

In [58]:
# 3 Point Field Goals by points and season
fg3_scatter = px.scatter(
    season_fg3_wins, x="points", y="three_point_percent", size = "win_percentage", 
    color="three_point_percent", animation_frame = "season", animation_group = "team_name", 
    hover_name = "team_name", size_max = 20, range_x=[80, 130], range_y=[20, 50]
)

fg3_scatter.show()
# 3 Point Percentage is spread out and highly differentiated in the early 2000s, with only
# a few teams having high percentages each year. 
# As the seasons progress, the groups converge and become more concentrated around higher 
# percentages, indicating a shift in play style. 

In [59]:
# Free Throws
query = """
        SELECT
            season,
            team_name,
            SUM(wins) AS wins,
            SUM(games_played) AS games,
            win_percentage,
            AVG(points) AS points,
            AVG(fta) AS free_throw_attempts,
            AVG(ftm) AS free_throws_made,
            AVG(ft_pct) AS free_throw_percent
        FROM
            avg_team_game_data
        GROUP BY
            season,
            team_name;
        """
season_ft_wins = pd.read_sql(query, conn)
season_ft_wins

season            team_name  wins  games  win_percentage      points  \
0      2000        Atlanta Hawks    25     82           17.07   90.963415   
1      2000       Boston Celtics    36     82           39.02   94.621951   
2      2000    Charlotte Hornets    46     82           43.90   91.939024   
3      2000        Chicago Bulls    15     82           12.20   87.573171   
4      2000  Cleveland Cavaliers    30     82           24.39   92.207317   
..      ...                  ...   ...    ...             ...         ...   
651    2022     Sacramento Kings    40     66           59.38  121.118566   
652    2022    San Antonio Spurs    17     67           18.18  111.245544   
653    2022      Toronto Raptors    32     68           34.29  112.410390   
654    2022            Utah Jazz    33     68           37.14  116.268398   
655    2022   Washington Wizards    31     68           44.44  111.638889   

     free_throw_attempts  free_throws_made  free_throw_percent  
0              22.085366         16.756098           76.557805  
1              26.707317         19.768293           73.633780  
2              26.170732         19.500000           74.324024  
3              23.280488         17.195122           73.680122  
4              24.878049         19.036585           76.637439  
..                   ...               ...                 ...  
651            25.431985         20.308824           80.388640  
652            20.883690         15.631016           74.663164  
653            24.187013         18.925974           78.231134  
654            23.986147         18.949351           78.470948  
655            22.343750         17.623264           79.477535  

[656 rows x 9 columns]

In [60]:
# Free Throws by points and season
ft_scatter = px.scatter(
    season_ft_wins, x="points", y="free_throw_percent", size = "win_percentage", 
    color="free_throw_percent", animation_frame = "season", animation_group = "team_name", 
    hover_name = "team_name", size_max = 20, range_x=[80, 130], range_y=[60, 90]
)

ft_scatter.show()
# A similar trend appears here, free throw percentage has a high deviation in the early 2000s,
# and teams begin to adapt comparable strategies as the percentage increases.
# However, both of these patterns need to take into account the attempts made of each shot type, 
# as there has likely been an increase in shot attempts over the years. 

In [61]:
# Other Stats
query = """
        SELECT
            season,
            team_name,
            SUM(wins) AS wins,
            SUM(games_played) AS games,
            win_percentage,
            AVG(points) AS points,
            AVG(rebounds) AS rebounds,
            AVG(assists) AS assists,
            AVG(steals) AS steals,
            AVG(blocks) AS blocks,
            AVG(turnovers) AS turnovers
        FROM
            avg_team_game_data
        GROUP BY
            season,
            team_name;
        """
season_other_wins = pd.read_sql(query, conn)
season_other_wins

season            team_name  wins  games  win_percentage      points  \
0      2000        Atlanta Hawks    25     82           17.07   90.963415   
1      2000       Boston Celtics    36     82           39.02   94.621951   
2      2000    Charlotte Hornets    46     82           43.90   91.939024   
3      2000        Chicago Bulls    15     82           12.20   87.573171   
4      2000  Cleveland Cavaliers    30     82           24.39   92.207317   
..      ...                  ...   ...    ...             ...         ...   
651    2022     Sacramento Kings    40     66           59.38  121.118566   
652    2022    San Antonio Spurs    17     67           18.18  111.245544   
653    2022      Toronto Raptors    32     68           34.29  112.410390   
654    2022            Utah Jazz    33     68           37.14  116.268398   
655    2022   Washington Wizards    31     68           44.44  111.638889   

      rebounds    assists    steals    blocks  turnovers  
0    42.902439  19.012195  7.731707  4.719512  16.682927  
1    39.804878  20.829268  9.378049  4.097561  15.670732  
2    44.402439  23.170732  8.109756  5.548780  14.426829  
3    38.853659  22.073171  8.231707  4.621951  15.756098  
4    42.134146  20.829268  7.829268  5.317073  16.463415  
..         ...        ...       ...       ...        ...  
651  41.991728  27.079963  7.056066  3.226103  14.075368  
652  42.941176  26.663547  6.883244  3.878342  15.460784  
653  42.719913  23.493506  9.327273  5.190909  11.950216  
654  45.017316  25.312554  6.371861  5.297835  15.477489  
655  43.046875  25.057292  6.793403  5.157986  14.187500  

[656 rows x 11 columns]

In [62]:
# Other Statistics by points and season

other_long = pd.melt(season_other_wins, 
                     id_vars = ["season", "team_name", "wins", "win_percentage"], 
                     value_vars = ["points", "rebounds", "assists", "steals", "blocks", "turnovers"], 
                     var_name = "Statistic", value_name = "Count"
                    )
other_scatter = px.scatter(other_long, x = "season", y = "Count", facet_col = "Statistic", 
                           opacity = 0.4, size = "win_percentage", size_max = 10, 
                           labels = {"Count": "Count", "season": "Season"}, 
                           title = "Scoring Statistics by Season", facet_col_wrap = 2
                          )
other_scatter.update_xaxes(nticks=20)
other_scatter.update_yaxes(matches = None)
other_scatter.for_each_yaxis(lambda yaxis: yaxis.update(showticklabels = True))
other_scatter.show()


In [63]:
# Other Statistics by points and season

other_long = pd.melt(season_other_wins, 
                     id_vars = ["season", "team_name", "wins", "win_percentage", "points"], 
                     value_vars = ["points", "rebounds", "assists", "steals", "blocks", "turnovers"], 
                     var_name = "Statistic", value_name = "Count"
                    )
other_scatter = px.scatter(other_long, x = "season", y = "Count",
                           opacity = 0.8, size = "win_percentage", size_max = 10, range_y = [0, 55], 
                           color = "Statistic", title = "Other Statistics by Season"
                          )
other_scatter.update_xaxes(nticks = 20, matches = None)
other_scatter.update_yaxes(nticks = 10, matches = None)
other_scatter.show()

In [64]:
print(team_avg_stats)

      season           team_name game_location        fga        fgm  \
0       2000       Atlanta Hawks          away  81.097561  33.682927   
1       2000       Atlanta Hawks          home  81.536585  36.463415   
2       2000      Boston Celtics          away  78.390244  33.780488   
3       2000      Boston Celtics          home  79.780488  33.853659   
4       2000   Charlotte Hornets          away  78.707317  33.341463   
...      ...                 ...           ...        ...        ...   
1307    2022     Toronto Raptors          home  90.393939  41.393939   
1308    2022           Utah Jazz          away  89.228571  42.028571   
1309    2022           Utah Jazz          home  88.060606  41.606061   
1310    2022  Washington Wizards          away  86.638889  42.138889   
1311    2022  Washington Wizards          home  83.687500  40.656250   

           fg2a       fg2m       fg3a       fg3m        fta  ...     ft_pct  \
0     70.682927  30.243902  10.414634   3.439024  21.073

In [65]:
# New Dataframe to group by season
query = """
        SELECT
            season,
            win_percentage,
            AVG(points) AS points,
            AVG(fga) AS field_goal_attempts,
            AVG(fgm) AS field_goals_made,
            AVG(fg_pct) AS field_goal_percent,
            AVG(fg2a) AS two_point_attempts,
            AVG(fg2m) AS two_points_made,
            AVG(fg2_pct) AS two_point_percent,
            AVG(fg3a) AS three_point_attempts,
            AVG(fg3a) AS three_point_attempts,
            AVG(fg3_pct) AS three_point_percent,
            AVG(fta) AS free_throw_attempts,
            AVG(ftm) AS free_throws_made,
            AVG(ft_pct) AS free_throw_percent,
            AVG(rebounds) AS rebounds,
            AVG(assists) AS assists,
            AVG(steals) AS steals,
            AVG(blocks) AS blocks,
            AVG(turnovers) AS turnovers
        FROM
            avg_team_game_data
        GROUP BY
            season;
        """
season_avg_stats = pd.read_sql(query, conn)
season_avg_stats

season  win_percentage      points  field_goal_attempts  field_goals_made  \
0     2000           17.07   94.810345            80.598823         35.687553   
1     2001           24.39   95.476451            81.271236         36.169470   
2     2002           21.95   95.080740            80.785955         35.717830   
3     2003           24.39   93.396552            79.815812         35.010093   
4     2004            9.76   97.198780            80.335772         35.949187   
5     2005           19.51   97.008537            78.989837         35.839837   
6     2006           29.27   98.739431            79.704472         36.528455   
7     2007           29.27   99.923171            81.504472         37.263821   
8     2008           39.02   99.950813            80.916260         37.117886   
9     2009           46.34  100.447154            81.702846         37.695122   
10    2010           48.78   99.550407            81.215447         37.245528   
11    2011           51.52   96.259596            81.426768         36.473737   
12    2012           46.34   98.058130            81.954878         37.106504   
13    2013           34.15  101.008943            82.996748         37.715041   
14    2014           60.98  100.014228            83.565041         37.515041   
15    2015           51.22  102.671545            84.572764         38.237805   
16    2016           48.78  105.590650            85.412195         39.049187   
17    2018           29.27  111.208537            89.210569         41.082114   
18    2019           18.18  111.686294            88.808235         40.828500   
19    2020           44.44  112.091204            88.418056         41.212963   
20    2021           39.02  110.615854            88.098374         40.621951   
21    2022           44.44  114.103753            87.906258         41.683109   

    field_goal_percent  two_point_attempts  two_points_made  \
0            44.415038           66.891085        30.841463   
1            44.616362           66.521867        30.954163   
2            44.306459           66.104710        30.587468   
3            43.937115           64.890664        29.828848   
4            44.856480           64.584553        30.348780   
5            45.483768           63.008943        30.113821   
6            45.927878           62.764634        30.460976   
7            45.798020           63.397154        30.709350   
8            45.956004           62.793089        30.470732   
9            46.258183           63.563821        31.263415   
10           45.973285           63.202033        30.787805   
11           44.884924           63.045455        30.063131   
12           45.398555           62.008943        29.950813   
13           45.575341           61.462602        29.969512   
14           45.006711           61.151626        29.669512   
15           45.326846           60.491057        29.720325   
16           45.820886           58.411789        29.395528   
17           46.140593           57.201626        29.718293   
18           46.081819           54.714366        28.638262   
19           46.689648           53.778241        28.515278   
20           46.195179           52.921545        28.183740   
21           47.548810           53.842979        29.404645   

    two_point_percent  three_point_attempts  three_point_attempts  \
0           46.284420             13.707738             13.707738   
1           46.672494             14.749369             14.749369   
2           46.409458             14.681245             14.681245   
3           46.057956             14.925147             14.925147   
4           47.160874             15.751220             15.751220   
5           47.957504             15.980894             15.980894   
6           48.695947             16.939837             16.939837   
7           48.607598             18.107317             18.107317   
8           48.668939             18.123171             18.123171   


In [66]:
# Conversion to long-form
season_long = pd.melt(season_avg_stats, 
                     id_vars = ["season", "win_percentage", "points"], 
                     value_vars = ["rebounds", "assists", "steals", "blocks", "turnovers"], 
                     var_name = "Statistic", value_name = "AVG"
                     )

season_hist = px.histogram(season_long, histfunc = 'avg', histnorm = 'percent', 
                           x = "season", y = "AVG", color = "Statistic", 
                           barmode = 'group', nbins = 21, 
                           range_y = [7, 10], width = 900, height = 500, 
                           title = "Normalized Average Non-Shooting Stats by Season"
                          )
# Express histogram
season_hist.update_layout(yaxis_title = None)
season_hist.update_layout(xaxis_title = "Season")

season_hist.update_layout(legend = dict(yanchor = "top", y = 1.1, xanchor = "left", x = 0.0))
season_hist.update_layout(legend = dict(orientation = "h"))
season_hist.show()

In [67]:
# Graph Objects Histogram using the same data

season_hist_go = go.Figure()

statistics = ["rebounds", "assists", "steals", "blocks", "turnovers"]
colors = ["#1f77b4", "#ff7f0e", "#2ca02c", "#d62728", "#9467bd"]

a = 0
b = 10
win_pct_norm = [(number - a)/(b - a) for number in season_avg_stats['win_percentage']]

for statistic, color in zip(statistics, colors):
    trace = go.Histogram(
        x = season_long[season_long["Statistic"] == statistic]["season"],
        y = season_long[season_long["Statistic"] == statistic]["AVG"],
        histfunc = "avg",
        histnorm = "percent",
        nbinsx = 21,
        name = statistic.capitalize(),
        marker_color = color
    )
    season_hist_go.add_trace(trace)

win_pct_norm = go.Scatter(
    x = season_avg_stats['season'], 
    y = win_pct_norm, 
    mode = 'lines', 
    name = 'Average Win Percentage'
)
season_hist_go.add_trace(win_pct_norm)

#y_range_min = season_avg_stats['win_percentage'].min()
#y_range_max = season_avg_stats['win_percentage'].max()

#average_win_percentage['win_percentage_normalized'] = (average_win_percentage['win_percentage'] - 
#                                                       win_percentage_min) / (win_percentage_max - 
#                                                                              win_percentage_min)

#season_hist_go.update_layout(
#    yaxis_range=[y_range_min, y_range_max]
#)

season_hist_go.update_layout(
    barmode = "group",
    xaxis_title = "Season",
    yaxis_title = None,
    title = "Normalized Average Non-Shooting Stats by Season",
    legend = dict(orientation = "h", xanchor = "left", x = 0, yanchor = "top", y = 1.1),
    width = 900,
    height = 500, 
    yaxis_range=[7, 10] # Comment out to see win % trend line
)

season_hist_go.show()

# This figure shows the significant increase in assists and rebounds over the years.

In [68]:
# From all seasonal data seen so far, the most signiifcant changes in statistics appear to be 
# 2-point attempts, 3-point attempts, rebounds, and asssists.
# (As well as the the increase in accuracy-percentage for each of these statistics)
# We also see overall points per game, field goal attempts, free-throw percentage, and win percentage.